In [23]:
import pandas as pd
from statistics import median
import csv
from projects import project_list

In [24]:
r_file_name = 'ci_skipped_dynamic_batching.csv'
result_file = open(r_file_name, 'w')
result_headers = ['project', 'algorithm', 'batch_size', 'builds_saved', 'median_delay', 'testall_size']
writer = csv.writer(result_file)
writer.writerow(result_headers)

69

In [25]:
batch_total = 0

In [26]:
def output_values(tr_results):
    l = []
    i = 0
    while i < len(tr_results):
        if tr_results[i] == 'passed':
            l.append(1)
        else:
            l.append(0)
        i += 1
    
    return l

In [27]:
def batchstop4(commits):
    global batch_total
    
    l = len(commits)//2
    
    batch_total += 1        
    
    if 0 in commits:
        
        if len(commits) == 4:
            batch_total += 4
            return commits[0] & commits[1] & commits[2] & commits[3]
        
        return batchbisect(commits[:l]) & batchbisect(commits[l:])
    
    return 1

In [28]:
def batchbisect(commits):
    global batch_total
    
    l = len(commits)//2
    
    batch_total += 1
    if len(commits) == 1:
        return commits[0]
    
    if 0 in commits:
        return batchbisect(commits[:l]) & batchbisect(commits[l:])
    
    return 1

In [29]:
def batchbisect_dynamic(commits):
    global batch_total
    
    batch_size = 16
    length = len(commits)
    builds = 0
    i = 0
    delays = []
    
    while i < length:
        batch = commits[i:i+batch_size]
        fails_per = 100*batch.count(0)/batch_size
        
        delays.extend([batch_size-x-1 for x in range(batch_size)])
        
        batch_total = 0
        res = batchbisect(batch)
        builds += batch_total
        print('Building {} {} {} {}'.format(batch_size, batch, batch_total, builds))
        
        i += batch_size
        
        if res == 0:
            
            if fails_per > 50 & batch[-1] == 0:
                #if batch has a lot of failures then definitely split
                
                if batch_size == 1:
                    continue
                else:
                    batch_size //= 2
            
            if fails_per < 20 & batch[-1] == 1:
                continue
        
        else:
            if batch_size == 16:
                continue
            else:
                batch_size *= 2
    
    return builds, delays
            

In [30]:
def batchstop4_dynamic(commits):
    global batch_total
    
    batch_size = 16
    length = len(commits)
    builds = 0
    i = 0
    delays = []
    
    while i < length:
        batch = commits[i:i+batch_size]
        fails_per = 100*batch.count(0)/batch_size
        delays.extend([batch_size-x-1 for x in range(batch_size)])
        
        batch_total = 0
        res = batchstop4(batch)
        builds += batch_total
        print('Building {} {} {} {}'.format(batch_size, batch, batch_total, builds))
        
        i += batch_size
        
        if res == 0:
            if fails_per > 50 & batch[-1] == 0:
                #if batch has a lot of failures then definitely split
                
                if batch_size == 4:
                    continue
                else:
                    batch_size //= 2
            
            if fails_per < 20 & batch[-1] == 1:
                continue
        
        else:
            if batch_size == 16:
                continue
            else:
                batch_size *= 2
    
    return builds, delays

In [31]:
for p in project_list:
    p_name = p.split('/')[1]
    try:
        data = pd.read_csv('ci_skip_data/extracted_project_travis/' + p_name)
    except:
        continue
    total_length = len(data) - 100
    data = data[ data['verdict'] == 0]
    data = data.iloc[100:]
    results = output_values(data['tr_status'].tolist())
    builds, delays = batchbisect_dynamic(results)
    reqd = 100-(100*builds/total_length)
    fr = 100*results.count(0)/total_length
    
    writer.writerow([p_name, 'BATCHBISECT', '-1', reqd, median(delays), total_length])
    
    

Building 16 [0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 11 11
Building 8 [1, 0, 1, 1, 1, 0, 1, 0] 13 24
Building 4 [1, 1, 1, 1] 1 25
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 26
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0] 11 37
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 38
Building 16 [1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 15 53
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 54
Building 16 [1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1] 15 69
Building 8 [1, 1, 1, 1, 1, 1, 0, 0] 7 76
Building 4 [0, 0, 0, 1] 7 83
Building 2 [0, 1] 3 86
Building 1 [1] 1 87
Building 2 [1, 1] 1 88
Building 4 [1, 1, 1, 0] 5 93
Building 2 [1, 0] 3 96
Building 1 [0] 1 97
Building 1 [0] 1 98
Building 1 [0] 1 99
Building 1 [1] 1 100
Building 2 [1, 0] 3 103
Building 1 [1] 1 104
Building 2 [1, 0] 3 107
Building 1 [1] 1 108
Building 2 [0, 1] 3 111
Building 1 [0] 1 112
Building 1 [1] 1 113
Building 2 [1, 1] 1 114
Building 4 [1, 1, 0, 0] 5 119
Building 2 [1, 1] 1 120
Building 4 [1, 1, 1, 1] 1 121
Build

Building 16 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] 31 31
Building 8 [0, 0, 0, 0, 0, 0, 0, 0] 15 46
Building 4 [0, 0, 0, 0] 7 53
Building 2 [0, 0] 3 56
Building 1 [0] 1 57
Building 1 [0] 1 58
Building 1 [0] 1 59
Building 1 [0] 1 60
Building 1 [0] 1 61
Building 1 [0] 1 62
Building 1 [0] 1 63
Building 1 [0] 1 64
Building 1 [0] 1 65
Building 1 [0] 1 66
Building 1 [0] 1 67
Building 1 [0] 1 68
Building 1 [0] 1 69
Building 1 [0] 1 70
Building 1 [0] 1 71
Building 1 [0] 1 72
Building 1 [0] 1 73
Building 1 [0] 1 74
Building 1 [0] 1 75
Building 1 [0] 1 76
Building 1 [0] 1 77
Building 1 [0] 1 78
Building 1 [0] 1 79
Building 1 [0] 1 80
Building 1 [0] 1 81
Building 1 [0] 1 82
Building 1 [0] 1 83
Building 1 [0] 1 84
Building 1 [0] 1 85
Building 1 [0] 1 86
Building 1 [0] 1 87
Building 1 [0] 1 88
Building 1 [0] 1 89
Building 1 [0] 1 90
Building 1 [0] 1 91
Building 1 [0] 1 92
Building 1 [0] 1 93
Building 1 [0] 1 94
Building 1 [0] 1 95
Building 1 [0] 1 96
Building 1 [0] 1 97
Building 1 [0] 1 98

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1] 9 9
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 10
Building 16 [1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1] 15 25
Building 8 [1, 1, 1, 0, 1, 1, 1, 1] 7 32
Building 4 [1, 1, 1, 1] 1 33
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 34
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 35
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 36
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1] 9 45
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 46
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 47
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 48
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 49
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1] 9 58
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 59
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1] 9 68
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 75
Building 4 [1, 1, 1, 1] 1 76
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 1
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 2
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1] 13 15
Building 8 [1, 0, 0, 0, 1, 1, 1, 1] 9 24
Building 4 [1, 1, 1, 1] 1 25
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 26
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 27
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 28
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 29
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0] 15 44
Building 8 [0, 1, 1, 1, 1, 1, 1, 1] 7 51
Building 4 [1, 1, 0, 0] 5 56
Building 2 [0, 0] 3 59
Building 1 [0] 1 60
Building 1 [0] 1 61
Building 1 [1] 1 62
Building 2 [1, 1] 1 63
Building 4 [1, 1, 1, 1] 1 64
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 65
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 66
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 67
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 1
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 2
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1] 11 13
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 14
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0] 9 23
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 24
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1] 11 35
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 36
Building 16 [1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 9 45
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 46
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 47
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 48
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 49
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 50
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 51
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 52
Building 16 [1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1

...

Building 1 [0] 1 5068
Building 1 [0] 1 5069
Building 1 [0] 1 5070
Building 1 [0] 1 5071
Building 1 [0] 1 5072
Building 1 [0] 1 5073
Building 1 [0] 1 5074
Building 1 [0] 1 5075
Building 1 [0] 1 5076
Building 1 [0] 1 5077
Building 1 [0] 1 5078
Building 1 [0] 1 5079
Building 1 [0] 1 5080
Building 1 [0] 1 5081
Building 1 [0] 1 5082
Building 1 [0] 1 5083
Building 1 [0] 1 5084
Building 1 [0] 1 5085
Building 1 [0] 1 5086
Building 1 [0] 1 5087
Building 1 [0] 1 5088
Building 1 [0] 1 5089
Building 1 [0] 1 5090
Building 1 [0] 1 5091
Building 1 [0] 1 5092
Building 1 [0] 1 5093
Building 1 [0] 1 5094
Building 1 [0] 1 5095
Building 1 [0] 1 5096
Building 1 [0] 1 5097
Building 1 [0] 1 5098
Building 1 [0] 1 5099
Building 1 [1] 1 5100
Building 2 [1, 1] 1 5101
Building 4 [1, 1, 1, 1] 1 5102
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 5103
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 5104
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 5105
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1,

Building 1 [0] 1 9918
Building 1 [0] 1 9919
Building 1 [0] 1 9920
Building 1 [0] 1 9921
Building 1 [0] 1 9922
Building 1 [0] 1 9923
Building 1 [0] 1 9924
Building 1 [0] 1 9925
Building 1 [0] 1 9926
Building 1 [0] 1 9927
Building 1 [0] 1 9928
Building 1 [0] 1 9929
Building 1 [0] 1 9930
Building 1 [0] 1 9931
Building 1 [0] 1 9932
Building 1 [0] 1 9933
Building 1 [0] 1 9934
Building 1 [0] 1 9935
Building 1 [0] 1 9936
Building 1 [0] 1 9937
Building 1 [0] 1 9938
Building 1 [0] 1 9939
Building 1 [0] 1 9940
Building 1 [0] 1 9941
Building 1 [0] 1 9942
Building 1 [0] 1 9943
Building 1 [0] 1 9944
Building 1 [0] 1 9945
Building 1 [0] 1 9946
Building 1 [0] 1 9947
Building 1 [0] 1 9948
Building 1 [0] 1 9949
Building 1 [0] 1 9950
Building 1 [0] 1 9951
Building 1 [0] 1 9952
Building 1 [0] 1 9953
Building 1 [0] 1 9954
Building 1 [0] 1 9955
Building 1 [0] 1 9956
Building 1 [0] 1 9957
Building 1 [0] 1 9958
Building 1 [0] 1 9959
Building 1 [0] 1 9960
Building 1 [0] 1 9961
Building 1 [0] 1 9962
Building 1

Building 1 [0] 1 14367
Building 1 [0] 1 14368
Building 1 [0] 1 14369
Building 1 [0] 1 14370
Building 1 [0] 1 14371
Building 1 [0] 1 14372
Building 1 [0] 1 14373
Building 1 [0] 1 14374
Building 1 [0] 1 14375
Building 1 [0] 1 14376
Building 1 [0] 1 14377
Building 1 [0] 1 14378
Building 1 [0] 1 14379
Building 1 [0] 1 14380
Building 1 [0] 1 14381
Building 1 [0] 1 14382
Building 1 [0] 1 14383
Building 1 [0] 1 14384
Building 1 [0] 1 14385
Building 1 [0] 1 14386
Building 1 [0] 1 14387
Building 1 [0] 1 14388
Building 1 [0] 1 14389
Building 1 [0] 1 14390
Building 1 [0] 1 14391
Building 1 [0] 1 14392
Building 1 [0] 1 14393
Building 1 [0] 1 14394
Building 1 [0] 1 14395
Building 1 [0] 1 14396
Building 1 [0] 1 14397
Building 1 [0] 1 14398
Building 1 [0] 1 14399
Building 1 [0] 1 14400
Building 1 [0] 1 14401
Building 1 [0] 1 14402
Building 1 [0] 1 14403
Building 1 [0] 1 14404
Building 1 [0] 1 14405
Building 1 [0] 1 14406
Building 1 [0] 1 14407
Building 1 [0] 1 14408
Building 1 [0] 1 14409
Building 1 

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 1
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 2
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 3
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 4
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1] 15 19
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 20
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0] 15 35
Building 8 [0, 0, 0, 1, 1, 1, 1, 1] 9 44
Building 4 [1, 1, 1, 1] 1 45
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 52
Building 4 [0, 0, 0, 1] 7 59
Building 2 [1, 1] 1 60
Building 4 [1, 1, 1, 1] 1 61
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 62
Building 16 [1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1] 17 79
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 80
Building 16 [1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 15 95
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 96
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 97
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6041
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6042
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6043
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6044
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6045
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6046
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6047
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6048
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6049
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6050
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6051
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6052
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6053
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 6054
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [32]:
for p in project_list:
    p_name = p.split('/')[1]
    try:
        data = pd.read_csv('ci_skip_data/extracted_project_travis/' + p_name)
    except:
        continue
    total_length = len(data) - 100
    data = data[ data['verdict'] == 0]
    data = data.iloc[100:]
    results = output_values(data['tr_status'].tolist())
    builds, delays = batchstop4_dynamic(results)
    reqd = 100-(100*builds/total_length)
    fr = 100*results.count(0)/total_length
    
    writer.writerow([p_name, 'BATCHSTOP4', '-1', reqd, median(delays), total_length])
    
    #print('{:>40} {:>10} {:>30} {:>10}'.format(p, len(results), reqd, median(delays)))

Building 16 [0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 11 11
Building 8 [1, 0, 1, 1, 1, 0, 1, 0] 13 24
Building 4 [1, 1, 1, 1] 1 25
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 26
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0] 11 37
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 38
Building 16 [1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 15 53
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 54
Building 16 [1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1] 15 69
Building 8 [1, 1, 1, 1, 1, 1, 0, 0] 7 76
Building 4 [0, 0, 0, 1] 5 81
Building 4 [0, 1, 1, 1] 5 86
Building 4 [1, 1, 1, 1] 1 87
Building 8 [0, 1, 0, 0, 0, 0, 1, 1] 13 100
Building 4 [0, 1, 1, 0] 5 105
Building 4 [1, 0, 1, 0] 5 110
Building 4 [1, 1, 1, 1] 1 111
Building 8 [1, 0, 0, 1, 1, 1, 1, 1] 9 120
Building 4 [1, 1, 1, 0] 5 125
Building 4 [0, 0, 0, 1] 5 130
Building 4 [1, 1, 1, 1] 1 131
Building 8 [1, 1, 0, 1, 1, 1, 1, 1] 7 138
Building 4 [0, 0, 0, 0] 5 143
Building 4 [0, 0, 0, 0] 5 148
Building 4 [0, 0, 0, 0] 5 153
Building 4 [0

Building 16 [0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 9 9
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 10
Building 16 [1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1] 27 37
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 44
Building 4 [0, 0, 0, 0] 5 49
Building 4 [0, 0, 0, 0] 5 54
Building 4 [0, 0, 0, 0] 5 59
Building 4 [0, 0, 0, 0] 5 64
Building 4 [0, 0, 0, 1] 5 69
Building 4 [1, 1, 1, 1] 1 70
Building 8 [0, 0, 0, 0, 0, 0, 0, 0] 15 85
Building 4 [0, 0, 0, 0] 5 90
Building 4 [0, 0, 0, 0] 5 95
Building 4 [0, 0, 0, 0] 5 100
Building 4 [0, 0, 0, 0] 5 105
Building 4 [0, 0, 0, 0] 5 110
Building 4 [0, 0, 0, 0] 5 115
Building 4 [0, 0, 0, 0] 5 120
Building 4 [0, 0, 0, 0] 5 125
Building 4 [0, 0, 0, 0] 5 130
Building 4 [0, 0, 0, 0] 5 135
Building 4 [0, 0, 0, 0] 5 140
Building 4 [0, 0, 0, 0] 5 145
Building 4 [0, 0, 0, 0] 5 150
Building 4 [0, 0, 0, 0] 5 155
Building 4 [0, 0, 0, 0] 5 160
Building 4 [0, 0, 0, 0] 5 165
Building 4 [0, 0, 0, 0] 5 170
Building 4 [0, 0, 0, 0] 5 175
Building 4 [0, 0, 0, 0] 5 180
Bu

Building 16 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] 31 31
Building 8 [0, 0, 0, 0, 0, 0, 0, 0] 15 46
Building 4 [0, 0, 0, 0] 5 51
Building 4 [0, 0, 0, 0] 5 56
Building 4 [0, 0, 0, 0] 5 61
Building 4 [0, 0, 0, 0] 5 66
Building 4 [0, 0, 0, 0] 5 71
Building 4 [0, 0, 0, 0] 5 76
Building 4 [0, 0, 0, 0] 5 81
Building 4 [0, 0, 0, 0] 5 86
Building 4 [0, 1, 0, 0] 5 91
Building 4 [0, 0, 0, 1] 5 96
Building 4 [0, 0, 0, 0] 5 101
Building 4 [0, 0, 0, 0] 5 106
Building 4 [1, 0, 0, 0] 5 111
Building 4 [0, 0, 0, 0] 5 116
Building 4 [0, 0, 0, 0] 5 121
Building 4 [0, 0, 0, 0] 5 126
Building 4 [0, 0, 0, 0] 5 131
Building 4 [0, 1, 1, 0] 5 136
Building 4 [1, 1, 1, 1] 1 137
Building 8 [1, 0, 1, 1, 1, 1, 1, 1] 7 144
Building 4 [1, 0, 1, 1] 5 149
Building 4 [0, 0, 1, 1] 5 154
Building 4 [1, 1, 1, 1] 1 155
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 156
Building 16 [1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0] 17 173
Building 8 [0, 0, 0, 0, 0, 0, 1, 1] 13 186
Building 4 [0, 0, 0, 0] 5 191
Building 4 [0, 0

Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 777
Building 4 [0, 1, 1, 1] 5 782
Building 4 [1, 1, 1, 1] 1 783
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 790
Building 4 [0, 1, 1, 0] 5 795
Building 4 [0, 0, 0, 1] 5 800
Building 4 [1, 1, 1, 1] 1 801
Building 8 [1, 0, 0, 1, 1, 1, 1, 0] 13 814
Building 4 [0, 1, 1, 0] 5 819
Building 4 [0, 0, 0, 1] 5 824
Building 4 [1, 1, 1, 1] 1 825
Building 8 [1, 0, 0, 1, 1, 1, 1, 1] 9 834
Building 4 [1, 0, 0, 1] 5 839
Building 4 [1, 1, 1, 1] 1 840
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 847
Building 4 [0, 0, 0, 1] 5 852
Building 4 [1, 0, 0, 0] 5 857
Building 4 [0, 1, 1, 1] 5 862
Building 4 [1, 1, 1, 0] 5 867
Building 4 [0, 1, 1, 1] 5 872
Building 4 [1, 1, 1, 1] 1 873
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 874
Building 16 [1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1] 15 889
Building 8 [1, 1, 1, 0, 0, 0, 0, 1] 13 902
Building 4 [1, 1, 1, 1] 1 903
Building 8 [1, 1, 1, 1, 1, 0, 0, 1] 9 912
Building 4 [1, 1, 1, 0] 5 917
Building 4 [0, 1, 1, 1] 5 922
Building 4 [1, 0, 0, 1] 

Building 16 [1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0] 15 15
Building 8 [1, 1, 1, 1, 1, 0, 1, 1] 7 22
Building 4 [1, 1, 1, 0] 5 27
Building 4 [1, 1, 0, 1] 5 32
Building 4 [1, 1, 1, 1] 1 33
Building 8 [1, 1, 1, 0, 1, 1, 1, 1] 7 40
Building 4 [1, 1, 0, 0] 5 45
Building 4 [0, 1, 1, 1] 5 50
Building 4 [1, 1, 1, 1] 1 51
Building 8 [1, 0, 1, 1, 1, 1, 1, 1] 7 58
Building 4 [1, 1, 1, 1] 1 59
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 60
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0] 9 69
Building 8 [0, 1, 1, 1, 1, 1, 1, 1] 7 76
Building 4 [1, 0, 1, 1] 5 81
Building 4 [1, 1, 1, 1] 1 82
Building 8 [1, 0, 0, 0, 0, 1, 1, 1] 13 95
Building 4 [1, 1, 1, 1] 1 96
Building 8 [1, 1, 1, 0, 1, 1, 1, 1] 7 103
Building 4 [1, 0, 1, 1] 5 108
Building 4 [1, 1, 1, 1] 1 109
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 110
Building 16 [1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] 23 133
Building 8 [0, 0, 0, 1, 1, 1, 0, 0] 13 146
Building 4 [1, 0, 1, 1] 5 151
Building 4 [1, 1, 1, 1] 1 152
Building 8 [1, 

...

Building 4 [0, 0, 0, 0] 5 7061
Building 4 [0, 0, 0, 0] 5 7066
Building 4 [0, 0, 0, 0] 5 7071
Building 4 [0, 0, 0, 0] 5 7076
Building 4 [0, 0, 0, 0] 5 7081
Building 4 [0, 0, 0, 0] 5 7086
Building 4 [0, 0, 0, 0] 5 7091
Building 4 [0, 0, 0, 0] 5 7096
Building 4 [0, 0, 0, 0] 5 7101
Building 4 [0, 0, 0, 0] 5 7106
Building 4 [0, 0, 0, 0] 5 7111
Building 4 [0, 0, 0, 0] 5 7116
Building 4 [0, 0, 0, 0] 5 7121
Building 4 [0, 0, 0, 0] 5 7126
Building 4 [0, 0, 0, 0] 5 7131
Building 4 [0, 0, 0, 0] 5 7136
Building 4 [0, 0, 0, 0] 5 7141
Building 4 [0, 0, 0, 0] 5 7146
Building 4 [0, 0, 0, 0] 5 7151
Building 4 [0, 0, 0, 0] 5 7156
Building 4 [0, 0, 0, 0] 5 7161
Building 4 [0, 0, 0, 0] 5 7166
Building 4 [0, 0, 0, 0] 5 7171
Building 4 [0, 0, 0, 0] 5 7176
Building 4 [0, 0, 0, 0] 5 7181
Building 4 [0, 0, 0, 0] 5 7186
Building 4 [0, 0, 0, 0] 5 7191
Building 4 [0, 0, 0, 0] 5 7196
Building 4 [0, 0, 0, 0] 5 7201
Building 4 [0, 0, 0, 0] 5 7206
Building 4 [0, 0, 0, 0] 5 7211
Building 4 [0, 0, 0, 0] 5 7216
Building

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0] 9 9
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 10
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1] 9 19
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 20
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1] 9 29
Building 8 [1, 1, 0, 0, 1, 1, 1, 1] 7 36
Building 4 [1, 1, 0, 0] 5 41
Building 4 [1, 1, 1, 1] 1 42
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 43
Building 16 [1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1] 11 54
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 55
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 56
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 57
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 58
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 59
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 60
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 61
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 62
Building 16

Building 4 [0, 0, 0, 0] 5 3534
Building 4 [0, 0, 0, 0] 5 3539
Building 4 [0, 0, 0, 0] 5 3544
Building 4 [0, 0, 0, 0] 5 3549
Building 4 [0, 0, 0, 0] 5 3554
Building 4 [0, 0, 0, 0] 5 3559
Building 4 [0, 0, 0, 0] 5 3564
Building 4 [0, 0, 0, 0] 5 3569
Building 4 [0, 0, 0, 0] 5 3574
Building 4 [0, 0, 0, 0] 5 3579
Building 4 [0, 0, 0, 0] 5 3584
Building 4 [0, 0, 0, 0] 5 3589
Building 4 [0, 0, 0, 0] 5 3594
Building 4 [0, 0, 0, 0] 5 3599
Building 4 [0, 0, 0, 0] 5 3604
Building 4 [0, 0, 0, 0] 5 3609
Building 4 [0, 0, 0, 0] 5 3614
Building 4 [0, 0, 0, 0] 5 3619
Building 4 [0, 0, 0, 0] 5 3624
Building 4 [0, 0, 0, 0] 5 3629
Building 4 [0, 0, 0, 0] 5 3634
Building 4 [0, 0, 0, 0] 5 3639
Building 4 [0, 0, 0, 0] 5 3644
Building 4 [0, 0, 0, 0] 5 3649
Building 4 [0, 0, 0, 0] 5 3654
Building 4 [0, 0, 0, 0] 5 3659
Building 4 [0, 0, 0, 0] 5 3664
Building 4 [0, 0, 0, 0] 5 3669
Building 4 [0, 0, 0, 0] 5 3674
Building 4 [0, 0, 0, 0] 5 3679
Building 4 [0, 0, 0, 0] 5 3684
Building 4 [0, 0, 0, 0] 5 3689
Building

Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 1
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 2
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 3
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 4
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1] 15 19
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 20
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0] 15 35
Building 8 [0, 0, 0, 1, 1, 1, 1, 1] 9 44
Building 4 [1, 1, 1, 1] 1 45
Building 8 [1, 1, 1, 1, 1, 1, 1, 0] 7 52
Building 4 [0, 0, 0, 1] 5 57
Building 4 [1, 1, 1, 1] 1 58
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 59
Building 16 [1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1] 17 76
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 77
Building 16 [1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1] 15 92
Building 8 [1, 1, 1, 1, 1, 1, 1, 1] 1 93
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 94
Building 16 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1] 1 95
Buildin

Building 4 [0, 0, 0, 0] 5 8205
Building 4 [0, 0, 0, 0] 5 8210
Building 4 [0, 0, 0, 0] 5 8215
Building 4 [0, 0, 0, 0] 5 8220
Building 4 [0, 0, 0, 0] 5 8225
Building 4 [0, 0, 0, 0] 5 8230
Building 4 [0, 0, 0, 0] 5 8235
Building 4 [0, 0, 0, 0] 5 8240
Building 4 [0, 0, 0, 0] 5 8245
Building 4 [0, 0, 0, 0] 5 8250
Building 4 [0, 0, 0, 0] 5 8255
Building 4 [0, 0, 0, 0] 5 8260
Building 4 [0, 0, 0, 0] 5 8265
Building 4 [0, 0, 0, 0] 5 8270
Building 4 [0, 0, 0, 0] 5 8275
Building 4 [0, 0, 0, 0] 5 8280
Building 4 [0, 0, 0, 0] 5 8285
Building 4 [0, 0, 0, 0] 5 8290
Building 4 [0, 0, 0, 0] 5 8295
Building 4 [0, 0, 0, 0] 5 8300
Building 4 [0, 0, 0, 0] 5 8305
Building 4 [0, 0, 0, 0] 5 8310
Building 4 [0, 0, 0, 0] 5 8315
Building 4 [0, 0, 0, 0] 5 8320
Building 4 [0, 0, 0, 0] 5 8325
Building 4 [0, 0, 0, 0] 5 8330
Building 4 [0, 0, 0, 0] 5 8335
Building 4 [0, 0, 0, 0] 5 8340
Building 4 [0, 0, 0, 0] 5 8345
Building 4 [0, 0, 0, 0] 5 8350
Building 4 [0, 0, 0, 0] 5 8355
Building 4 [0, 0, 0, 0] 5 8360
Building

In [33]:
for p in project_list:
    p_name = p.split('/')[1]
    try:
        data = pd.read_csv('ci_skip_data/extracted_project_travis/' + p_name)
    except:
        continue
    total_length = len(data) - 100
    data = data[ data['verdict'] == 0]
    data = data.iloc[100:]
    
    ci_skipped = len(data)
    print(total_length - ci_skipped, p_name)

31 BuildCraft-BuildCraft.csv
33 apache-tajo.csv
371 osmdroid-osmdroid.csv
61 DSpace-DSpace.csv
119 apache-nifi.csv
679 caelum-vraptor4.csv
94 grails-grails-core.csv
58 square-wire.csv
216 puniverse-quasar.csv
66 dropwizard-dropwizard.csv
220 essentials-Essentials.csv
63 mybatis-mybatis-3.csv
219 naver-pinpoint.csv
74 FasterXML-jackson-databind.csv
136 samtools-htsjdk.csv
0 deeplearning4j-deeplearning4j.csv
130 open-keychain-open-keychain.csv
742 yegor256-takes.csv
150 keycloak-keycloak.csv
232 rackerlabs-blueflood.csv
171 xetorthio-jedis.csv
214 orbeon-orbeon-forms.csv
225 linkedin-gobblin.csv
325 JabRef-jabref.csv
226 jOOQ-jOOQ.csv
217 structr-structr.csv
0 floragunncom-search-guard.csv
52 SpongePowered-SpongeForge.csv
309 sakaiproject-sakai.csv
577 dreamhead-moco.csv
442 nutzam-nutz.csv
355 CloudSlang-cloud-slang.csv
155 geotools-geotools.csv
79 CloudifySource-cloudify.csv
23 SpongePowered-SpongeCommon.csv
883 apache-zeppelin.csv
890 typetools-checker-framework.csv
237 geoserver-geos